In [1]:
import ee
import geemap
import eemont
from osgeo import ogr, osr

In [2]:
try:
    ee.Initialize()
except Exception as e:
    ee.Authenticate()
    ee.Initialize()

In [18]:
def shpTOfc(pathToShape):
    import json
    # Open the shapefile, get the layer
    ds = ogr.Open(pathToShape)
    lyr = ds.GetLayer()
    # Create an emtpy feature collection
    fc = ee.FeatureCollection([])
    # Get the feature fields and geometries and add them to the feature collection
    idCount = 1
    for feat in lyr:
        geom = feat.geometry()
        # Automatic coordinate transformation
        from_sr = lyr.GetSpatialRef()
        to_sr = osr.SpatialReference()
        to_sr.ImportFromEPSG(4326)
        cs = osr.CoordinateTransformation(from_sr, to_sr)
        geom.Transform(cs)
        geojson = json.loads(geom.ExportToJson())
        properties = {}
        for i in range(feat.GetFieldCount()):
            field_name = feat.GetFieldDefnRef(i).GetName()
            field_value = feat.GetField(i)
            properties[field_name] = field_value
        ee_feat = ee.Feature(ee.Geometry(geojson), properties)
        # Remove the 'id' property from the feature
        ee_feat = ee_feat.set('id', idCount)
        idCount += 1
        fc = fc.merge(ee.FeatureCollection(ee_feat))
    return fc

def fcTOcsv(json, outPath):
    import pandas as pd
    flag = 0
    featVals = json['features']
    for f in featVals:
        prop = f['properties']
        if flag == 0:
            # Create a pandas data frame with the first element of the values
            out_pd = pd.DataFrame(prop, index=[0])
            flag = 1
        else:
            out_pd = pd.concat([out_pd, pd.DataFrame(prop, index=[0])])
    # Write the pandas dataframe 
    out_pd.to_csv(outPath, index=False)  

In [4]:
Map = geemap.Map(zoom=4)
Map.add_basemap('TERRAIN') # add Google Earth Basemap
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [7]:
###Cargo un shapefile manual
fc = ee.FeatureCollection('projects/ee-mvgonzalez/assets/SELS')

In [8]:
gfw = ee.Image("projects/ee-mvgonzalez/assets/landcoverSA").clip(fc)

In [14]:
Map.addLayer(gfw,  {'bands': ['b2'], 'min': 0, 'max': 17, 'palette': ['05450a', '086a10', '54a708', '78d203', '009900', 'c6b044', 'dcd159',
    'dade48', 'fbff13', 'b6ff05', '27ff87', 'c24f44', 'a5a5a5', 'ff6d4c',
    '69fff8', 'f9ffa4', '1c0dff']}, 'Land Cover Modis')

In [15]:
# Apply the reduction
values = gfw.reduceRegions(fc, ee.Reducer.count(), 1000).getInfo()
values

{'type': 'FeatureCollection',
 'columns': {'Name': 'String',
  'altitudeMo': 'String',
  'b1': 'Long<0, 4294967295>',
  'b10': 'Long<0, 4294967295>',
  'b11': 'Long<0, 4294967295>',
  'b12': 'Long<0, 4294967295>',
  'b13': 'Long<0, 4294967295>',
  'b14': 'Long<0, 4294967295>',
  'b15': 'Long<0, 4294967295>',
  'b16': 'Long<0, 4294967295>',
  'b17': 'Long<0, 4294967295>',
  'b18': 'Long<0, 4294967295>',
  'b19': 'Long<0, 4294967295>',
  'b2': 'Long<0, 4294967295>',
  'b20': 'Long<0, 4294967295>',
  'b21': 'Long<0, 4294967295>',
  'b3': 'Long<0, 4294967295>',
  'b4': 'Long<0, 4294967295>',
  'b5': 'Long<0, 4294967295>',
  'b6': 'Long<0, 4294967295>',
  'b7': 'Long<0, 4294967295>',
  'b8': 'Long<0, 4294967295>',
  'b9': 'Long<0, 4294967295>',
  'begin': 'String',
  'descriptio': 'String',
  'end': 'String',
  'extrude': 'Long',
  'icon': 'String',
  'system:index': 'String',
  'tessellate': 'Long',
  'timestamp': 'String',
  'visibility': 'Long'},
 'features': [{'type': 'Feature',
   'geo

In [19]:
csv1 = fcTOcsv(values, 'C:/Users/musimundo/Documents/SRI/reducer_lc.csv')